In [273]:
import pandas as pd
import glob, os
from pandas.io.json import json_normalize as jn
import itertools
import json
import requests
import bz2

In [2]:
# Set view parameters
pd.set_option('display.max_rows', 500)
pd.set_option('display.max_columns', 500)
pd.set_option('display.width', 1000)

In [3]:
path = '/Users/henry/code/freelance/upwork/04.03_betfair_download/data'

In [142]:
# ALTERNATIVE
# files_lists = [glob.glob(os.path.join(path, dir + '/*.bz2')) for dir in dirs]
# files = list(itertools.chain(*files_lists))

In [4]:
files = glob.glob(os.path.join(path + '/**/*.bz2'), recursive=True)

In [27]:
files = glob.glob(os.path.join(path + '/201811M/*.bz2'))

In [245]:
# TEMPORARY - FOR TESTING ONLY
# test_file = test_files[8]
test_file = 'data/201808M/1.144859492.bz2'

#### Uncompress bz2 data into bytes with BZ2File.read()

In [268]:
uncompressedData = bz2.BZ2File(test_file).read()

In [269]:
type(uncompressedData)

bytes

#### Turn bytes into string with .decode()

In [284]:
data = uncompressedData.decode('utf8')

#### Read bz2 into df with pd.read_json

In [297]:
df = pd.read_json(test_file, lines=True, compression='bz2')

In [298]:
df.shape

(974, 4)

In [299]:
df.columns

Index(['clk', 'mc', 'op', 'pt'], dtype='object')

In [300]:
# Change column names
df.columns = ['sequence_token', 'market_change', 'operation_type', 'published_time']

In [331]:
# Expand market_change column into df
market_change = jn(df['market_change'][0])

for x in range(1, df.shape[0]):
    flat = jn(df['market_change'][x])
    market_change = market_change.append(flat)

In [332]:
market_change.shape

(974, 31)

In [335]:
market_change.info()

<class 'pandas.core.frame.DataFrame'>
Int64Index: 974 entries, 0 to 0
Data columns (total 31 columns):
id                                        974 non-null object
marketDefinition.betDelay                 10 non-null float64
marketDefinition.bettingType              10 non-null object
marketDefinition.bspMarket                10 non-null object
marketDefinition.bspReconciled            10 non-null object
marketDefinition.complete                 10 non-null object
marketDefinition.countryCode              10 non-null object
marketDefinition.crossMatching            10 non-null object
marketDefinition.discountAllowed          10 non-null object
marketDefinition.eventId                  10 non-null object
marketDefinition.eventName                10 non-null object
marketDefinition.eventTypeId              10 non-null object
marketDefinition.inPlay                   10 non-null object
marketDefinition.marketBaseRate           10 non-null float64
marketDefinition.marketTime             

In [343]:
market_change.dropna(axis=0, subset=['marketDefinition.bettingType']).reset_index(drop=True)

id  marketDefinition.betDelay marketDefinition.bettingType marketDefinition.bspMarket marketDefinition.bspReconciled marketDefinition.complete marketDefinition.countryCode marketDefinition.crossMatching marketDefinition.discountAllowed marketDefinition.eventId marketDefinition.eventName marketDefinition.eventTypeId marketDefinition.inPlay  marketDefinition.marketBaseRate marketDefinition.marketTime marketDefinition.marketType marketDefinition.name  marketDefinition.numberOfActiveRunners  marketDefinition.numberOfWinners marketDefinition.openDate marketDefinition.persistenceEnabled marketDefinition.regulators                           marketDefinition.runners marketDefinition.runnersVoidable marketDefinition.settledTime marketDefinition.status marketDefinition.suspendTime marketDefinition.timezone marketDefinition.turnInPlayEnabled  marketDefinition.version                                                 rc
0  1.144859492                        0.0                         ODDS                      False                          False                      True                           GB                           True                             True                 28774943            Reading v Derby                            1                   False                              5.0    2018-08-03T19:00:00.000Z                  MATCH_ODDS            Match Odds                                     3.0                               1.0  2018-08-03T19:00:00.000Z                                True                    [MR_INT]  [{'status': 'ACTIVE', 'sortPriority': 1, 'id':...                            False                          NaN                    OPEN     2018-08-03T19:00:00.000Z             Europe/London                               True              2.266324e+09                                                NaN
1  1.144859492                        7.0                         ODDS                      False                          False                      True                           GB                           True                             True                 28774943            Reading v Derby                            1                    True                              5.0    2018-08-03T19:00:00.000Z                  MATCH_ODDS            Match Odds                                     3.0                               1.0  2018-08-03T19:00:00.000Z                                True                    [MR_INT]  [{'status': 'ACTIVE', 'sortPriority': 1, 'id':...                            False                          NaN                    OPEN     2018-08-03T19:00:00.000Z             Europe/London                               True              2.322390e+09  [{'ltp': 3.55, 'id': 58805}, {'ltp': 3.85, 'id...
2  1.144859492                        1.0                         ODDS                      False                          False                      True                           GB                           True                             True                 28774943            Reading v Derby                            1                    True                              5.0    2018-08-03T19:00:00.000Z                  MATCH_ODDS            Match Odds                                     3.0                               1.0  2018-08-03T19:00:00.000Z                                True                    [MR_INT]  [{'status': 'ACTIVE', 'sortPriority': 1, 'id':...                            False                          NaN                    OPEN     2018-08-03T19:00:00.000Z             Europe/London                               True              2.322481e+09                       [{'ltp': 2.44, 'id': 58805}]
3  1.144859492                        7.0                         ODDS                      False                          False                      True                           GB                           True                             True                 28774943            

In [347]:
df.join(market_change).drop('market_change', axis=1).dropna(axis=0, subset=['marketDefinition.bettingType']).reset_index(drop=True)

sequence_token operation_type  published_time           id  marketDefinition.betDelay marketDefinition.bettingType marketDefinition.bspMarket marketDefinition.bspReconciled marketDefinition.complete marketDefinition.countryCode marketDefinition.crossMatching marketDefinition.discountAllowed marketDefinition.eventId marketDefinition.eventName marketDefinition.eventTypeId marketDefinition.inPlay  marketDefinition.marketBaseRate marketDefinition.marketTime marketDefinition.marketType marketDefinition.name  marketDefinition.numberOfActiveRunners  marketDefinition.numberOfWinners marketDefinition.openDate marketDefinition.persistenceEnabled marketDefinition.regulators                           marketDefinition.runners marketDefinition.runnersVoidable marketDefinition.settledTime marketDefinition.status marketDefinition.suspendTime marketDefinition.timezone marketDefinition.turnInPlayEnabled  marketDefinition.version                                                 rc
0      6861105503            mcm   1529585281561  1.144859492                        0.0                         ODDS                      False                          False                      True                           GB                           True                             True                 28774943            Reading v Derby                            1                   False                              5.0    2018-08-03T19:00:00.000Z                  MATCH_ODDS            Match Odds                                     3.0                               1.0  2018-08-03T19:00:00.000Z                                True                    [MR_INT]  [{'status': 'ACTIVE', 'sortPriority': 1, 'id':...                            False                          NaN                    OPEN     2018-08-03T19:00:00.000Z             Europe/London                               True              2.266324e+09                                                NaN
1      6861105503            mcm   1529585281561  1.144859492                        7.0                         ODDS                      False                          False                      True                           GB                           True                             True                 28774943            Reading v Derby                            1                    True                              5.0    2018-08-03T19:00:00.000Z                  MATCH_ODDS            Match Odds                                     3.0                               1.0  2018-08-03T19:00:00.000Z                                True                    [MR_INT]  [{'status': 'ACTIVE', 'sortPriority': 1, 'id':...                            False                          NaN                    OPEN     2018-08-03T19:00:00.000Z             Europe/London                               True              2.322390e+09  [{'ltp': 3.55, 'id': 58805}, {'ltp': 3.85, 'id...
2      6861105503            mcm   1529585281561  1.144859492                        1.0                         ODDS                      False                          False                      True                           GB                           True                             True                 28774943            Reading v Derby                            1                    True                              5.0    2018-08-03T19:00:00.000Z                  MATCH_ODDS            Match Odds                                     3.0                               1.0  2018-08-03T19:00:00.000Z                                True                    [MR_INT]  [{'status': 'ACTIVE', 'sortPriority': 1, 'id':...                            False                          NaN                    OPEN     2018-08-03T19:00:00.000Z             Europe/London                               True              2.322481e+09                       [{'ltp': 2.44, 'id': 58805}]
3      6861105503            mcm   1529585281561  1.144859492                        7.

In [334]:
market_change.head(10)

id  marketDefinition.betDelay marketDefinition.bettingType marketDefinition.bspMarket marketDefinition.bspReconciled marketDefinition.complete marketDefinition.countryCode marketDefinition.crossMatching marketDefinition.discountAllowed marketDefinition.eventId marketDefinition.eventName marketDefinition.eventTypeId marketDefinition.inPlay  marketDefinition.marketBaseRate marketDefinition.marketTime marketDefinition.marketType marketDefinition.name  marketDefinition.numberOfActiveRunners  marketDefinition.numberOfWinners marketDefinition.openDate marketDefinition.persistenceEnabled marketDefinition.regulators                           marketDefinition.runners marketDefinition.runnersVoidable marketDefinition.settledTime marketDefinition.status marketDefinition.suspendTime marketDefinition.timezone marketDefinition.turnInPlayEnabled  marketDefinition.version                                                 rc
0  1.144859492                        0.0                         ODDS                      False                          False                      True                           GB                           True                             True                 28774943            Reading v Derby                            1                   False                              5.0    2018-08-03T19:00:00.000Z                  MATCH_ODDS            Match Odds                                     3.0                               1.0  2018-08-03T19:00:00.000Z                                True                    [MR_INT]  [{'status': 'ACTIVE', 'sortPriority': 1, 'id':...                            False                          NaN                    OPEN     2018-08-03T19:00:00.000Z             Europe/London                               True              2.266324e+09                                                NaN
0  1.144859492                        NaN                          NaN                        NaN                            NaN                       NaN                          NaN                            NaN                              NaN                      NaN                        NaN                          NaN                     NaN                              NaN                         NaN                         NaN                   NaN                                     NaN                               NaN                       NaN                                 NaN                         NaN                                                NaN                              NaN                          NaN                     NaN                          NaN                       NaN                                NaN                       NaN                        [{'ltp': 3.3, 'id': 58805}]
0  1.144859492                        NaN                          NaN                        NaN                            NaN                       NaN                          NaN                            NaN                              NaN                      NaN                        NaN                          NaN                     NaN                              NaN                         NaN                         NaN                   NaN                                     NaN                               NaN                       NaN                                 NaN                         NaN                                                NaN                              NaN                          NaN                     NaN                          NaN                       NaN                                NaN                       NaN                       [{'ltp': 2.84, 'id': 48325}]
0  1.144859492                        NaN                          NaN                        NaN                            NaN                       NaN                          NaN                            NaN                              NaN                      NaN            

In [309]:
df2.shape

(974, 1)

In [310]:
df2.head()

market_change
0              id  marketDefinition.betDelay mark...
1              id                           rc
0 ...
2              id                            rc
0...
3              id                             rc
...
4              id                                ...

In [315]:
with bz2.open(test_file, "rt") as f:
    d=json.loads(f.decode())
    
f.close()

AttributeError: '_io.TextIOWrapper' object has no attribute 'decode'

In [248]:
with bz2.open(test_file, "rt") as f:
    testlist = [line.rstrip('\n') for line in f]
    
f.close()

In [249]:
testlist

['{"op":"mcm","clk":"6861105503","pt":1529585281561,"mc":[{"id":"1.144859492","marketDefinition":{"bspMarket":false,"turnInPlayEnabled":true,"persistenceEnabled":true,"marketBaseRate":5.0,"eventId":"28774943","eventTypeId":"1","numberOfWinners":1,"bettingType":"ODDS","marketType":"MATCH_ODDS","marketTime":"2018-08-03T19:00:00.000Z","suspendTime":"2018-08-03T19:00:00.000Z","bspReconciled":false,"complete":true,"inPlay":false,"crossMatching":true,"runnersVoidable":false,"numberOfActiveRunners":3,"betDelay":0,"status":"OPEN","runners":[{"status":"ACTIVE","sortPriority":1,"id":103122,"name":"Reading"},{"status":"ACTIVE","sortPriority":2,"id":48325,"name":"Derby"},{"status":"ACTIVE","sortPriority":3,"id":58805,"name":"The Draw"}],"regulators":["MR_INT"],"countryCode":"GB","discountAllowed":true,"timezone":"Europe/London","openDate":"2018-08-03T19:00:00.000Z","version":2266323587,"name":"Match Odds","eventName":"Reading v Derby"}}]}',
 '{"op":"mcm","clk":"6926639337","pt":1530732266658,"mc":

In [259]:
json_list = [json.loads(x) for x in testlist]

In [260]:
df_list = []

for j in json_list:
    temp = jn(j)
    temp2 = temp.join(jn(temp['mc'][0]))
    df_list.append(temp2)

In [263]:
json_df = pd.concat(df_list).reset_index(drop=True)

/anaconda3/lib/python3.7/site-packages/ipykernel_launcher.py:1: FutureWarning: Sorting because non-concatenation axis is not aligned. A future version
of pandas will change to not sort by default.

To accept the future behavior, pass 'sort=False'.

To retain the current behavior and silence the warning, pass 'sort=True'.

  """Entry point for launching an IPython kernel.


In [264]:
json_df.head()

clk           id  marketDefinition.betDelay marketDefinition.bettingType marketDefinition.bspMarket marketDefinition.bspReconciled marketDefinition.complete marketDefinition.countryCode marketDefinition.crossMatching marketDefinition.discountAllowed marketDefinition.eventId marketDefinition.eventName marketDefinition.eventTypeId marketDefinition.inPlay  marketDefinition.marketBaseRate marketDefinition.marketTime marketDefinition.marketType marketDefinition.name  marketDefinition.numberOfActiveRunners  marketDefinition.numberOfWinners marketDefinition.openDate marketDefinition.persistenceEnabled marketDefinition.regulators                           marketDefinition.runners marketDefinition.runnersVoidable marketDefinition.settledTime marketDefinition.status marketDefinition.suspendTime marketDefinition.timezone marketDefinition.turnInPlayEnabled  marketDefinition.version                                                 mc   op             pt  \
0  6861105503  1.144859492                        0.0                         ODDS                      False                          False                      True                           GB                           True                             True                 28774943            Reading v Derby                            1                   False                              5.0    2018-08-03T19:00:00.000Z                  MATCH_ODDS            Match Odds                                     3.0                               1.0  2018-08-03T19:00:00.000Z                                True                    [MR_INT]  [{'status': 'ACTIVE', 'sortPriority': 1, 'id':...                            False                          NaN                    OPEN     2018-08-03T19:00:00.000Z             Europe/London                               True              2.266324e+09  [{'id': '1.144859492', 'marketDefinition': {'b...  mcm  1529585281561   
1  6926639337  1.144859492                        NaN                          NaN                        NaN                            NaN                       NaN                          NaN                            NaN                              NaN                      NaN                        NaN                          NaN                     NaN                              NaN                         NaN                         NaN                   NaN                                     NaN                               NaN                       NaN                                 NaN                         NaN                                                NaN                              NaN                          NaN                     NaN                          NaN                       NaN                                NaN                       NaN  [{'id': '1.144859492', 'rc': [{'ltp': 3.3, 'id...  mcm  1530732266658   
2  6926751095  1.144859492                        NaN                          NaN                        NaN                            NaN                       NaN                          NaN                            NaN                              NaN                      NaN                        NaN                          NaN                     NaN                              NaN                         NaN                         NaN                   NaN                                     NaN                               NaN                       NaN                                 NaN                         NaN                                                NaN                              NaN                          NaN                     NaN                          NaN                       NaN                                NaN                       NaN  [{'id': '1.144859492', 'rc': [{'ltp': 2.84, 'i...  mcm  1530733540223   
3  6926946560  1.144859492                        NaN                          NaN                        NaN                            NaN  

In [212]:
z = json_list[1]

In [213]:
json_list[1]

{'op': 'mcm',
 'clk': '8041171867',
 'pt': 1542790384398,
 'mc': [{'id': '1.151141363',
   'marketDefinition': {'bspMarket': False,
    'turnInPlayEnabled': True,
    'persistenceEnabled': True,
    'marketBaseRate': 5.0,
    'eventId': '29007111',
    'eventTypeId': '1',
    'numberOfWinners': 1,
    'bettingType': 'ODDS',
    'marketType': 'TEAM_A_1',
    'marketTime': '2018-11-24T15:00:00.000Z',
    'suspendTime': '2018-11-24T15:00:00.000Z',
    'bspReconciled': False,
    'complete': True,
    'inPlay': False,
    'crossMatching': True,
    'runnersVoidable': False,
    'numberOfActiveRunners': 3,
    'betDelay': 0,
    'status': 'OPEN',
    'runners': [{'status': 'ACTIVE',
      'sortPriority': 1,
      'id': 6760258,
      'name': 'Aldershot +1'},
     {'status': 'ACTIVE',
      'sortPriority': 2,
      'id': 6872417,
      'name': 'Barrow -1'},
     {'status': 'ACTIVE', 'sortPriority': 3, 'id': 151478, 'name': 'Draw'}],
    'regulators': ['MR_INT'],
    'countryCode': 'GB',
    

In [214]:
top_level = jn(z)

In [215]:
top_level = top_level.join(jn(top_level['mc'][0]))

In [216]:
len(top_level['mc'])

1

In [217]:
top_level

clk                                                 mc   op             pt           id  marketDefinition.betDelay marketDefinition.bettingType  marketDefinition.bspMarket  marketDefinition.bspReconciled  marketDefinition.complete marketDefinition.countryCode  marketDefinition.crossMatching  marketDefinition.discountAllowed marketDefinition.eventId marketDefinition.eventName marketDefinition.eventTypeId  marketDefinition.inPlay  marketDefinition.marketBaseRate marketDefinition.marketTime marketDefinition.marketType marketDefinition.name  marketDefinition.numberOfActiveRunners  marketDefinition.numberOfWinners marketDefinition.openDate  marketDefinition.persistenceEnabled marketDefinition.regulators                           marketDefinition.runners  marketDefinition.runnersVoidable marketDefinition.status marketDefinition.suspendTime marketDefinition.timezone  marketDefinition.turnInPlayEnabled  marketDefinition.version
0  8041171867  [{'id': '1.151141363', 'marketDefinition': {'b...  mcm  1542790384398  1.151141363                          0                         ODDS                       False                           False                       True                           GB                            True                              True                 29007111         Aldershot v Barrow                            1                    False                              5.0    2018-11-24T15:00:00.000Z                    TEAM_A_1          Aldershot +1                                       3                                 1  2018-11-24T15:00:00.000Z                                 True                    [MR_INT]  [{'status': 'ACTIVE', 'sortPriority': 1, 'id':...                             False                    OPEN     2018-11-24T15:00:00.000Z             Europe/London                                True                2523483106

In [223]:
len(json_list)

194

In [230]:
crazy = pd.concat(df_list).reset_index(drop=True)

/anaconda3/lib/python3.7/site-packages/ipykernel_launcher.py:1: FutureWarning: Sorting because non-concatenation axis is not aligned. A future version
of pandas will change to not sort by default.

To accept the future behavior, pass 'sort=False'.

To retain the current behavior and silence the warning, pass 'sort=True'.

  """Entry point for launching an IPython kernel.


In [236]:
crazy.loc[:5]

clk           id  marketDefinition.betDelay marketDefinition.bettingType marketDefinition.bspMarket marketDefinition.bspReconciled marketDefinition.complete marketDefinition.countryCode marketDefinition.crossMatching marketDefinition.discountAllowed marketDefinition.eventId marketDefinition.eventName marketDefinition.eventTypeId marketDefinition.inPlay  marketDefinition.marketBaseRate marketDefinition.marketTime marketDefinition.marketType marketDefinition.name  marketDefinition.numberOfActiveRunners  marketDefinition.numberOfWinners marketDefinition.openDate marketDefinition.persistenceEnabled marketDefinition.regulators                           marketDefinition.runners marketDefinition.runnersVoidable marketDefinition.settledTime marketDefinition.status marketDefinition.suspendTime marketDefinition.timezone marketDefinition.turnInPlayEnabled  marketDefinition.version                                                 mc   op             pt                            rc
0  7980140729  1.151141321                        0.0                         ODDS                      False                          False                      True                           GB                           True                             True                 29007111         Aldershot v Barrow                            1                   False                              5.0    2018-11-24T15:00:00.000Z               OVER_UNDER_25  Over/Under 2.5 Goals                                     2.0                               1.0  2018-11-24T15:00:00.000Z                                True                    [MR_INT]  [{'status': 'ACTIVE', 'sortPriority': 1, 'id':...                            False                          NaN                    OPEN     2018-11-24T15:00:00.000Z             Europe/London                               True              2.512030e+09  [{'id': '1.151141321', 'marketDefinition': {'b...  mcm  1542031325087                           NaN
1  8041171867  1.151141363                        0.0                         ODDS                      False                          False                      True                           GB                           True                             True                 29007111         Aldershot v Barrow                            1                   False                              5.0    2018-11-24T15:00:00.000Z                    TEAM_A_1          Aldershot +1                                     3.0                               1.0  2018-11-24T15:00:00.000Z                                True                    [MR_INT]  [{'status': 'ACTIVE', 'sortPriority': 1, 'id':...                            False                          NaN                    OPEN     2018-11-24T15:00:00.000Z             Europe/London                               True              2.523483e+09  [{'id': '1.151141363', 'marketDefinition': {'b...  mcm  1542790384398                           NaN
2  8045258261  1.151141311                        NaN                          NaN                        NaN                            NaN                       NaN                          NaN                            NaN                              NaN                      NaN                        NaN                          NaN                     NaN                              NaN                         NaN                         NaN                   NaN                                     NaN                               NaN                       NaN                                 NaN                         NaN                                                NaN                              NaN                          NaN                     NaN                          NaN                       NaN                                NaN                       NaN  [{'id': '1.151141311', 'rc': [{'ltp': 2.18, 'i...  mcm  1542837706343  [{'ltp': 2.18, 'id': 62504}]
3  8049386558  1.151141320        

In [148]:
for x in top_level['marketDefinition.runners']:
    print(x)

[{'status': 'ACTIVE', 'sortPriority': 1, 'id': 256383, 'name': 'Rochdale'}, {'status': 'ACTIVE', 'sortPriority': 2, 'id': 422179, 'name': 'Accrington'}, {'status': 'ACTIVE', 'sortPriority': 3, 'id': 58805, 'name': 'The Draw'}]


In [149]:
for x in top_level['marketDefinition.runners']:
    top_level = top_level.join(jn(x), rsuffix='_x')

In [150]:
jn(top_level['marketDefinition.runners'][0])

id        name  sortPriority  status
0  256383    Rochdale             1  ACTIVE
1  422179  Accrington             2  ACTIVE
2   58805    The Draw             3  ACTIVE

In [129]:
top_level

clk                                                 mc   op             pt           id  marketDefinition.betDelay marketDefinition.bettingType  marketDefinition.bspMarket  marketDefinition.bspReconciled  marketDefinition.complete marketDefinition.countryCode  marketDefinition.crossMatching  marketDefinition.discountAllowed marketDefinition.eventId marketDefinition.eventName marketDefinition.eventTypeId  marketDefinition.inPlay  marketDefinition.marketBaseRate marketDefinition.marketTime marketDefinition.marketType marketDefinition.name  marketDefinition.numberOfActiveRunners  marketDefinition.numberOfWinners marketDefinition.openDate  marketDefinition.persistenceEnabled marketDefinition.regulators                           marketDefinition.runners  marketDefinition.runnersVoidable marketDefinition.status marketDefinition.suspendTime marketDefinition.timezone  marketDefinition.turnInPlayEnabled  marketDefinition.version    id_x      name  sortPriority  status
0  7956024199  [{'id': '1.151300360', 'marketDefinition': {'b...  mcm  1542617234961  1.151300360                          0                         ODDS                       False                           False                       True                           GB                            True                              True                 29012050      Rochdale v Accrington                            1                    False                              5.0    2018-11-24T15:00:00.000Z                  MATCH_ODDS            Match Odds                                       3                                 1  2018-11-24T15:00:00.000Z                                 True                    [MR_INT]  [{'status': 'ACTIVE', 'sortPriority': 1, 'id':...                             False                    OPEN     2018-11-24T15:00:00.000Z             Europe/London                                True                2521746538  256383  Rochdale             1  ACTIVE

In [79]:
b

id  marketDefinition.betDelay marketDefinition.bettingType  marketDefinition.bspMarket  marketDefinition.bspReconciled  marketDefinition.complete marketDefinition.countryCode  marketDefinition.crossMatching  marketDefinition.discountAllowed marketDefinition.eventId marketDefinition.eventName marketDefinition.eventTypeId  marketDefinition.inPlay  marketDefinition.marketBaseRate marketDefinition.marketTime marketDefinition.marketType marketDefinition.name  marketDefinition.numberOfActiveRunners  marketDefinition.numberOfWinners marketDefinition.openDate  marketDefinition.persistenceEnabled marketDefinition.regulators                           marketDefinition.runners  marketDefinition.runnersVoidable marketDefinition.status marketDefinition.suspendTime marketDefinition.timezone  marketDefinition.turnInPlayEnabled  marketDefinition.version
0  1.151300360                          0                         ODDS                       False                           False                       True                           GB                            True                              True                 29012050      Rochdale v Accrington                            1                    False                              5.0    2018-11-24T15:00:00.000Z                  MATCH_ODDS            Match Odds                                       3                                 1  2018-11-24T15:00:00.000Z                                 True                    [MR_INT]  [{'status': 'ACTIVE', 'sortPriority': 1, 'id':...                             False                    OPEN     2018-11-24T15:00:00.000Z             Europe/London                                True                2521746538
1  1.151300380                          0                         ODDS                       False                           False                       True                           GB                            True                              True                 29012050      Rochdale v Accrington                            1                    False                              5.0    2018-11-24T15:00:00.000Z               OVER_UNDER_25  Over/Under 2.5 Goals                                       2                                 1  2018-11-24T15:00:00.000Z                                 True                    [MR_INT]  [{'status': 'ACTIVE', 'sortPriority': 1, 'id':...                             False                    OPEN     2018-11-24T15:00:00.000Z             Europe/London                                True                2521746489

In [84]:
b['marketDefinition.runners']

0    [{'status': 'ACTIVE', 'sortPriority': 1, 'id':...
1    [{'status': 'ACTIVE', 'sortPriority': 1, 'id':...
Name: marketDefinition.runners, dtype: object

In [82]:
c = jn(b['marketDefinition.runners'][0])

c

id        name  sortPriority  status
0  256383    Rochdale             1  ACTIVE
1  422179  Accrington             2  ACTIVE
2   58805    The Draw             3  ACTIVE

In [83]:
d = jn(b['marketDefinition.runners'][1])

d

id             name  sortPriority  status
0  47972  Under 2.5 Goals             1  ACTIVE
1  47973   Over 2.5 Goals             2  ACTIVE

In [68]:
type(test)

bytes

In [26]:
bz2.decompress(test)

OSError: Invalid data stream

In [23]:
dec = bz2.BZ2Decompressor()

In [24]:
dec.decompress(test)

OSError: Invalid data stream

In [69]:
json.loads(testlist[0])

{'op': 'mcm',
 'clk': '7956024199',
 'pt': 1542617234961,
 'mc': [{'id': '1.151300360',
   'marketDefinition': {'bspMarket': False,
    'turnInPlayEnabled': True,
    'persistenceEnabled': True,
    'marketBaseRate': 5.0,
    'eventId': '29012050',
    'eventTypeId': '1',
    'numberOfWinners': 1,
    'bettingType': 'ODDS',
    'marketType': 'MATCH_ODDS',
    'marketTime': '2018-11-24T15:00:00.000Z',
    'suspendTime': '2018-11-24T15:00:00.000Z',
    'bspReconciled': False,
    'complete': True,
    'inPlay': False,
    'crossMatching': True,
    'runnersVoidable': False,
    'numberOfActiveRunners': 3,
    'betDelay': 0,
    'status': 'OPEN',
    'runners': [{'status': 'ACTIVE',
      'sortPriority': 1,
      'id': 256383,
      'name': 'Rochdale'},
     {'status': 'ACTIVE',
      'sortPriority': 2,
      'id': 422179,
      'name': 'Accrington'},
     {'status': 'ACTIVE', 'sortPriority': 3, 'id': 58805, 'name': 'The Draw'}],
    'regulators': ['MR_INT'],
    'countryCode': 'GB',
    

In [59]:
from io import StringIO

In [60]:
s = str(uncompressedData, 'utf-8')

In [61]:
data = StringIO(s)

In [33]:
uncompressedData = bz2.BZ2File(test_file, 'rb').read()

In [54]:
type(uncompressedData)

bytes

In [56]:
plz = uncompressedData.decode()

In [57]:
plz

'{"op":"mcm","clk":"7956024199","pt":1542617234961,"mc":[{"id":"1.151300360","marketDefinition":{"bspMarket":false,"turnInPlayEnabled":true,"persistenceEnabled":true,"marketBaseRate":5.0,"eventId":"29012050","eventTypeId":"1","numberOfWinners":1,"bettingType":"ODDS","marketType":"MATCH_ODDS","marketTime":"2018-11-24T15:00:00.000Z","suspendTime":"2018-11-24T15:00:00.000Z","bspReconciled":false,"complete":true,"inPlay":false,"crossMatching":true,"runnersVoidable":false,"numberOfActiveRunners":3,"betDelay":0,"status":"OPEN","runners":[{"status":"ACTIVE","sortPriority":1,"id":256383,"name":"Rochdale"},{"status":"ACTIVE","sortPriority":2,"id":422179,"name":"Accrington"},{"status":"ACTIVE","sortPriority":3,"id":58805,"name":"The Draw"}],"regulators":["MR_INT"],"countryCode":"GB","discountAllowed":true,"timezone":"Europe/London","openDate":"2018-11-24T15:00:00.000Z","version":2521746538,"name":"Match Odds","eventName":"Rochdale v Accrington"}},{"id":"1.151300380","marketDefinition":{"bspMarke

In [58]:
plz2 = pd.read_csv(plz)

FileNotFoundError: File b'{"op":"mcm","clk":"7956024199","pt":1542617234961,"mc":[{"id":"1.151300360","marketDefinition":{"bspMarket":false,"turnInPlayEnabled":true,"persistenceEnabled":true,"marketBaseRate":5.0,"eventId":"29012050","eventTypeId":"1","numberOfWinners":1,"bettingType":"ODDS","marketType":"MATCH_ODDS","marketTime":"2018-11-24T15:00:00.000Z","suspendTime":"2018-11-24T15:00:00.000Z","bspReconciled":false,"complete":true,"inPlay":false,"crossMatching":true,"runnersVoidable":false,"numberOfActiveRunners":3,"betDelay":0,"status":"OPEN","runners":[{"status":"ACTIVE","sortPriority":1,"id":256383,"name":"Rochdale"},{"status":"ACTIVE","sortPriority":2,"id":422179,"name":"Accrington"},{"status":"ACTIVE","sortPriority":3,"id":58805,"name":"The Draw"}],"regulators":["MR_INT"],"countryCode":"GB","discountAllowed":true,"timezone":"Europe/London","openDate":"2018-11-24T15:00:00.000Z","version":2521746538,"name":"Match Odds","eventName":"Rochdale v Accrington"}},{"id":"1.151300380","mar

In [48]:
plz = pd.read_csv(test_file, compression='bz2', header=None, delimiter='/n')

/anaconda3/lib/python3.7/site-packages/ipykernel_launcher.py:1: ParserWarning: Falling back to the 'python' engine because the 'c' engine does not support regex separators (separators > 1 char and different from '\s+' are interpreted as regex); you can avoid this warning by specifying engine='python'.
  """Entry point for launching an IPython kernel.


In [49]:
plz[0][0]

'{"op":"mcm","clk":"7956024199","pt":1542617234961,"mc":[{"id":"1.151300360","marketDefinition":{"bspMarket":false,"turnInPlayEnabled":true,"persistenceEnabled":true,"marketBaseRate":5.0,"eventId":"29012050","eventTypeId":"1","numberOfWinners":1,"bettingType":"ODDS","marketType":"MATCH_ODDS","marketTime":"2018-11-24T15:00:00.000Z","suspendTime":"2018-11-24T15:00:00.000Z","bspReconciled":false,"complete":true,"inPlay":false,"crossMatching":true,"runnersVoidable":false,"numberOfActiveRunners":3,"betDelay":0,"status":"OPEN","runners":[{"status":"ACTIVE","sortPriority":1,"id":256383,"name":"Rochdale"},{"status":"ACTIVE","sortPriority":2,"id":422179,"name":"Accrington"},{"status":"ACTIVE","sortPriority":3,"id":58805,"name":"The Draw"}],"regulators":["MR_INT"],"countryCode":"GB","discountAllowed":true,"timezone":"Europe/London","openDate":"2018-11-24T15:00:00.000Z","version":2521746538,"name":"Match Odds","eventName":"Rochdale v Accrington"}},{"id":"1.151300380","marketDefinition":{"bspMarke

In [50]:
type(plz[0][0])

str

In [34]:
plz = pd.read_csv(uncompressedData, compression='bz2', header=None, delimiter='\n')

OSError: [Errno 63] File name too long: b'{"op":"mcm","clk":"7956024199","pt":1542617234961,"mc":[{"id":"1.151300360","marketDefinition":{"bspMarket":false,"turnInPlayEnabled":true,"persistenceEnabled":true,"marketBaseRate":5.0,"eventId":"29012050","eventTypeId":"1","numberOfWinners":1,"bettingType":"ODDS","marketType":"MATCH_ODDS","marketTime":"2018-11-24T15:00:00.000Z","suspendTime":"2018-11-24T15:00:00.000Z","bspReconciled":false,"complete":true,"inPlay":false,"crossMatching":true,"runnersVoidable":false,"numberOfActiveRunners":3,"betDelay":0,"status":"OPEN","runners":[{"status":"ACTIVE","sortPriority":1,"id":256383,"name":"Rochdale"},{"status":"ACTIVE","sortPriority":2,"id":422179,"name":"Accrington"},{"status":"ACTIVE","sortPriority":3,"id":58805,"name":"The Draw"}],"regulators":["MR_INT"],"countryCode":"GB","discountAllowed":true,"timezone":"Europe/London","openDate":"2018-11-24T15:00:00.000Z","version":2521746538,"name":"Match Odds","eventName":"Rochdale v Accrington"}},{"id":"1

In [34]:
with bz2.BZ2File(file, "w") as fp:
    fp.write('\n'.join('123456789'))

NameError: name 'file' is not defined

In [35]:
test_file

'/Users/henry/code/freelance/upwork/04.03_betfair_download/data/201811M/1.150748476.bz2'

In [36]:
test_df = pd.read_csv('./data/201811M/1.150748476.bz2', delimiter='\n', compression='bz2', header=None)

EmptyDataError: No columns to parse from file

In [82]:
test_df['try'] = test_df[0].apply(lambda x: x.split(' '))

In [46]:
test_df[0]

0     {"op":"mcm","clk":"7914627839","pt":1541351777...
1     {"op":"mcm","clk":"7925026417","pt":1541499893...
2     {"op":"mcm","clk":"7926918366","pt":1541524725...
3     {"op":"mcm","clk":"7926949070","pt":1541525289...
4     {"op":"mcm","clk":"7927619418","pt":1541532973...
5     {"op":"mcm","clk":"7927640350","pt":1541533224...
6     {"op":"mcm","clk":"7927646147","pt":1541533285...
7     {"op":"mcm","clk":"7927659212","pt":1541533439...
8     {"op":"mcm","clk":"7927672475","pt":1541533586...
9     {"op":"mcm","clk":"7927694632","pt":1541533704...
10    {"op":"mcm","clk":"7927730945","pt":1541534005...
11    {"op":"mcm","clk":"7927761039","pt":1541534246...
12    {"op":"mcm","clk":"7927822272","pt":1541534649...
13    {"op":"mcm","clk":"7927883166","pt":1541535131...
14    {"op":"mcm","clk":"7927912857","pt":1541535378...
15    {"op":"mcm","clk":"7927930691","pt":1541535445...
16    {"op":"mcm","clk":"7928057512","pt":1541536460...
17    {"op":"mcm","clk":"7928088348","pt":154153

In [45]:
jn(jn(json.loads(test_df[0][0]))['mc'][0])

id  marketDefinition.betDelay marketDefinition.bettingType  marketDefinition.bspMarket  marketDefinition.bspReconciled  marketDefinition.complete marketDefinition.countryCode  marketDefinition.crossMatching  marketDefinition.discountAllowed marketDefinition.eventId        marketDefinition.eventName marketDefinition.eventTypeId  marketDefinition.inPlay  marketDefinition.marketBaseRate marketDefinition.marketTime marketDefinition.marketType marketDefinition.name  marketDefinition.numberOfActiveRunners  marketDefinition.numberOfWinners marketDefinition.openDate  marketDefinition.persistenceEnabled marketDefinition.regulators                           marketDefinition.runners  marketDefinition.runnersVoidable marketDefinition.status marketDefinition.suspendTime marketDefinition.timezone  marketDefinition.turnInPlayEnabled  marketDefinition.version
0  1.150748476                          0                         ODDS                       False                           False                       True                           GB                            True                              True                 28994313  Bromley FC B v Faversham Town FC                            1                    False                              5.0    2018-11-06T19:45:00.000Z                  MATCH_ODDS            Match Odds                                       3                                 1  2018-11-06T19:45:00.000Z                                 True                    [MR_INT]  [{'status': 'ACTIVE', 'sortPriority': 1, 'id':...                             False                    OPEN     2018-11-06T19:45:00.000Z             Europe/London                                True                2497471235

In [47]:
import bz2

In [48]:
uncompressedData = bz2.BZ2File(test_file).read()

In [49]:
uncompressedData

b'{"op":"mcm","clk":"7914627839","pt":1541351777499,"mc":[{"id":"1.150748476","marketDefinition":{"bspMarket":false,"turnInPlayEnabled":true,"persistenceEnabled":true,"marketBaseRate":5.0,"eventId":"28994313","eventTypeId":"1","numberOfWinners":1,"bettingType":"ODDS","marketType":"MATCH_ODDS","marketTime":"2018-11-06T19:45:00.000Z","suspendTime":"2018-11-06T19:45:00.000Z","bspReconciled":false,"complete":true,"inPlay":false,"crossMatching":true,"runnersVoidable":false,"numberOfActiveRunners":3,"betDelay":0,"status":"OPEN","runners":[{"status":"ACTIVE","sortPriority":1,"id":16356932,"name":"Bromley FC B"},{"status":"ACTIVE","sortPriority":2,"id":8380345,"name":"Faversham Town FC"},{"status":"ACTIVE","sortPriority":3,"id":58805,"name":"The Draw"}],"regulators":["MR_INT"],"countryCode":"GB","discountAllowed":true,"timezone":"Europe/London","openDate":"2018-11-06T19:45:00.000Z","version":2497471235,"name":"Match Odds","eventName":"Bromley FC B v Faversham Town FC"}}]}\n{"op":"mcm","clk":"7

In [68]:
x = bz2.BZ2File('./data/201811M/1.150748476.bz2')

AttributeError: 'BZ2File' object has no attribute 'decode'

In [88]:
x.close()

In [79]:
bz2.decompress(x)

TypeError: a bytes-like object is required, not 'BZ2File'

In [61]:
dec = bz2.BZ2Decompressor()

In [67]:
dec.decompress(x)

TypeError: a bytes-like object is required, not 'BZ2File'

------------------------------------------------------------

In [55]:
import numpy as np

In [59]:
df = pd.DataFrame(data)

In [ ]:
# Create a dtype with the binary data format and the desired column names
dt = np.dtype([('a', 'i4'), ('b', 'i4'), ('c', 'i4'), ('d', 'f4'), ('e', 'i4'),
               ('f', 'i4', (256,))])
data = np.fromfile(file, dtype=dt)
df = pd.DataFrame(data)

# Or if you want to explicitly set the column names
df = pd.DataFrame(data, columns=data.dtype.names)

In [64]:
pd.read_json(test_file, compression='bz2')

ValueError: Trailing data

In [40]:
pd.read_csv(test_file, header=None, compression='bz2')

ParserError: Error tokenizing data. C error: Expected 43 fields in line 29, saw 44


In [15]:
test = pd.read_csv(file[0], sep='\n', header=None)

NameError: name 'file' is not defined

In [13]:
json.loads(test[0][0])

NameError: name 'test' is not defined

In [61]:
df = pd.concat(map(pd.read_csv, glob.glob(os.path.join('~/Users/user/Desktop/data/xds/historic/BASIC/', "*.bz2"))))

ValueError: Invalid file path or buffer object type: <class 'list'>

In [44]:
pd.read_csv('/Users/user/Desktop/data/xds/historic/BASIC/27427374/1.118390406', sep='\n')

{"op":"mcm","clk":"640647816","pt":1430338452167,"mc":[{"id":"1.118390406","marketDefinition":{"bspMarket":false,"turnInPlayEnabled":false,"persistenceEnabled":true,"marketBaseRate":5.0,"eventId":"27427374","eventTypeId":"1","numberOfWinners":1,"bettingType":"ODDS","marketType":"MATCH_ODDS","marketTime":"2015-04-30T17:00:00.000Z","suspendTime":"2015-04-30T17:00:00.000Z","bspReconciled":false,"complete":true,"inPlay":false,"crossMatching":true,"runnersVoidable":false,"numberOfActiveRunners":3,"betDelay":0,"status":"OPEN","runners":[{"status":"ACTIVE","sortPriority":1,"id":579439,"name":"Brabrand"},{"status":"ACTIVE","sortPriority":2,"id":4886887,"name":"Middelfart"},{"status":"ACTIVE","sortPriority":3,"id":58805,"name":"The Draw"}],"regulators":["MR_INT"],"countryCode":"DK","discountAllowed":true,"timezone":"Europe/London","openDate":"2015-04-30T17:00:00.000Z","version":966296765,"name":"Match Odds","eventName":"Brabrand v Middelfart"}}]}
0  {"op":"mcm","clk":"640931146","pt":14303417671...                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                     
1  {"op":"mcm","clk":"641780997","pt":14303595189...                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                     
2  {"op":"mcm","clk":"644018648","pt":14304067792...                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                     
3  {"op":"mcm","clk":"644247721","pt":14304089699...                                                                                                                                      

In [16]:
data_df = pd.read_csv('data.tar', header=0, error_bad_lines=False)

b'Skipping line 3: expected 1 fields, saw 2\nSkipping line 6: expected 1 fields, saw 2\nSkipping line 11: expected 1 fields, saw 3\nSkipping line 15: expected 1 fields, saw 4\nSkipping line 26: expected 1 fields, saw 3\nSkipping line 28: expected 1 fields, saw 3\nSkipping line 31: expected 1 fields, saw 2\nSkipping line 40: expected 1 fields, saw 2\nSkipping line 41: expected 1 fields, saw 2\nSkipping line 48: expected 1 fields, saw 2\nSkipping line 49: expected 1 fields, saw 2\nSkipping line 60: expected 1 fields, saw 2\nSkipping line 61: expected 1 fields, saw 2\nSkipping line 70: expected 1 fields, saw 3\nSkipping line 71: expected 1 fields, saw 2\nSkipping line 73: expected 1 fields, saw 3\nSkipping line 77: expected 1 fields, saw 2\nSkipping line 78: expected 1 fields, saw 2\nSkipping line 80: expected 1 fields, saw 5\nSkipping line 82: expected 1 fields, saw 3\nSkipping line 86: expected 1 fields, saw 2\nSkipping line 87: expected 1 fields, saw 2\nSkipping line 89: expected 1 fie

ParserError: Error tokenizing data. C error: Buffer overflow caught - possible malformed input file.


In [15]:
data_df.head()

Empty DataFrame
Columns: [Unnamed: 0]
Index: []

In [12]:
test_two = pd.read_csv('test_two.tar.cpgz')

UnicodeDecodeError: 'utf-8' codec can't decode byte 0x8b in position 1: invalid start byte

In [11]:
test_two.head()

Empty DataFrame
Columns: [Unnamed: 0]
Index: []